In [1]:
#!pip install requests
#!pip install beautifulsoup4

In [73]:
import pandas as pd
import numpy as np
import requests
import urllib
import re
from bs4 import BeautifulSoup
import bs4

In [74]:
import os
currentPath = os.getcwd()
print(currentPath)

C:\Users\ohike\VS Code\bigkinds_crawler


In [75]:
df_news = pd.read_excel(r'E:\내 드라이브\greenwashing_company\consolidated\df_news_esgkeywords.xlsx')

In [76]:
df_news

Unnamed: 0        뉴스 식별자        일자   언론사                          기고자  \
0            217  2.100101e+06  20220302  매일경제                          NaN   
1            318  2.100601e+06  20200831  한국경제        임호범(lhb@hankyung.com)   
2            344  1.100401e+06  20200728  동아일보                          김민범   
3            346  2.100101e+06  20200728  매일경제                          신미진   
4            787  2.100101e+06  20210525  매일경제                          이새봄   
...          ...           ...       ...   ...                          ...   
3646      160610  1.100101e+06  20180417  경향신문  이진주 기자 jinju@kyunghyang.com   
3647      160611  2.100601e+06  20180417  한국경제                          김예랑   
3648      160850  2.100601e+06  20171228  한국경제                          김근희   
3649      161699  1.100901e+06  20191224  중앙일보                          권선미   
3650      162189  2.100101e+06  20180201  매일경제                          NaN   

                                           제목     통합 분류1     통합 분류2  \
0                  동원산업 환경 안전 최우선으로 ESG 경영 실천      지역>부산      지역>경남   
1                        강원도 동원산업과 스마트 양식장 조성     경제>반도체      경제>무역   
2     동원산업 친환경 노르웨이 양식 스타트업에 65억원 투자 지분 97 확보     경제>반도체   경제>취업_창업   
3                동원산업 노르웨이 연어 양식 스타트업에 65억 투자      지역>울산      경제>무역   
4                   한솔제지 건강기능식품 친환경 패키지 개발 나서  경제>서비스_쇼핑      경제>유통   
...                                       ...        ...        ...   
3646              세계 첫 태양광 방음터널 서울 동부간선도로에 설치      경제>유통        NaN   
3647    전력 생산 방음 효과 동시에 동부간선도로 태양광 방음터널 세계 최초    경제>국제경제     경제>반도체   
3648                      SDN 충청에너지서비스와 계약 체결     경제>부동산      경제>유통   
3649        제약바이오 시련 딛고 다시 일어서  혁신 신약 개발 집중하다   IT_과학>과학        NaN   
3650                코스닥 공시 에스맥  엑세스바이오  이테크건설      지역>울산      지역>경기   

         통합 분류3 사건/사고 분류1  ...  \
0      경제>산업_기업       NaN  ...   
1           NaN       NaN  ...   
2        경제>자동차       NaN  ...   
3         지역>경남       NaN  ...   
4           NaN       NaN  ...   
...         ...       ...  ...   
3646        NaN       NaN  ...   
3647        NaN       NaN  ...   
3648     경제>자동차       NaN  ...   
3649        NaN       NaN  ...   
3650      지역>강원       NaN  ...   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         키워드  \
0                                                                                     동원산업,환경,안전,최우선,실천,ESG,경영,한국,존경,기업,수산기업,최대,수산,기업,동원산업,경영,활동,확립,현장,안전,체계,ESG,경영,환경,사회,투명경영,박차,동원산업,글로벌,수산,기업,지속가능경영,논의,회의체,SeaBOS,Seafood,Business,Ocean,Stewardship,유일,한국,기업,해양,플라스틱,리더,기업,환경영향,저감,활동,안전,가치,안전,재해,통합,TF,설치,안전보건관리위원회,확대,개편,동원산업,노력,한국능률협회컨설팅,선정,한국,존경,기업,수산,1위,연속,동원산업,보전,해양,생태,환경,지역,사회,ESG,경영,일환,데이,국제,해안,클린업,International,Coastal,Clean-up,행사,진행,국제,해안,클린업,데이,행사,SeaBOS,회원사들,합의,감축,달성,해양,플라스틱,감축,달성,기획,국제,해안,클린업,데이,행사,서울,부산,해외,사업장,참여,진행,

In [65]:
#Uncomment to export the original dataframe into the excel format
#df_news.to_excel("output.xlsx")

In [77]:
#Drop unnecessary column & Change column name
df_news = df_news.drop(['Unnamed: 0'], axis=1)
df_news.columns = df_news.columns.str.replace('본문', '본문 미리보기')

In [78]:
#Set as :20 to make a small sample
df_news = df_news.iloc[:]

In [79]:
pd.set_option('display.max_colwidth', None)
df_news['URL'].astype(str)
df_news['URL'].fillna('NaN')

0                                     http://news.mk.co.kr/newsRead.php?no=193115&year=2022
1                                    https://www.hankyung.com/society/article/2020083170991
2                               https://www.donga.com/news/article/all/20200728/102201130/1
3                                     http://news.mk.co.kr/newsRead.php?no=769135&year=2020
4                                     http://news.mk.co.kr/newsRead.php?no=502125&year=2021
                                               ...                                         
3646    http://news.khan.co.kr/kh_news/khan_art_view.html?artid=201804172114005&code=620101
3647                                         http://news.hankyung.com/article/2018041768217
3648                                                                                    NaN
3649                                            https://www.joongang.co.kr/article/23664343
3650                                   http://news.mk.co.kr/newsRead.php?year=20

In [80]:
print(df_news['URL'])

0                                     http://news.mk.co.kr/newsRead.php?no=193115&year=2022
1                                    https://www.hankyung.com/society/article/2020083170991
2                               https://www.donga.com/news/article/all/20200728/102201130/1
3                                     http://news.mk.co.kr/newsRead.php?no=769135&year=2020
4                                     http://news.mk.co.kr/newsRead.php?no=502125&year=2021
                                               ...                                         
3646    http://news.khan.co.kr/kh_news/khan_art_view.html?artid=201804172114005&code=620101
3647                                         http://news.hankyung.com/article/2018041768217
3648                                                                                    NaN
3649                                            https://www.joongang.co.kr/article/23664343
3650                                   http://news.mk.co.kr/newsRead.php?year=20

In [81]:
df_news

뉴스 식별자        일자   언론사                          기고자  \
0     2.100101e+06  20220302  매일경제                          NaN   
1     2.100601e+06  20200831  한국경제        임호범(lhb@hankyung.com)   
2     1.100401e+06  20200728  동아일보                          김민범   
3     2.100101e+06  20200728  매일경제                          신미진   
4     2.100101e+06  20210525  매일경제                          이새봄   
...            ...       ...   ...                          ...   
3646  1.100101e+06  20180417  경향신문  이진주 기자 jinju@kyunghyang.com   
3647  2.100601e+06  20180417  한국경제                          김예랑   
3648  2.100601e+06  20171228  한국경제                          김근희   
3649  1.100901e+06  20191224  중앙일보                          권선미   
3650  2.100101e+06  20180201  매일경제                          NaN   

                                           제목     통합 분류1     통합 분류2  \
0                  동원산업 환경 안전 최우선으로 ESG 경영 실천      지역>부산      지역>경남   
1                        강원도 동원산업과 스마트 양식장 조성     경제>반도체      경제>무역   
2     동원산업 친환경 노르웨이 양식 스타트업에 65억원 투자 지분 97 확보     경제>반도체   경제>취업_창업   
3                동원산업 노르웨이 연어 양식 스타트업에 65억 투자      지역>울산      경제>무역   
4                   한솔제지 건강기능식품 친환경 패키지 개발 나서  경제>서비스_쇼핑      경제>유통   
...                                       ...        ...        ...   
3646              세계 첫 태양광 방음터널 서울 동부간선도로에 설치      경제>유통        NaN   
3647    전력 생산 방음 효과 동시에 동부간선도로 태양광 방음터널 세계 최초    경제>국제경제     경제>반도체   
3648                      SDN 충청에너지서비스와 계약 체결     경제>부동산      경제>유통   
3649        제약바이오 시련 딛고 다시 일어서  혁신 신약 개발 집중하다   IT_과학>과학        NaN   
3650                코스닥 공시 에스맥  엑세스바이오  이테크건설      지역>울산      지역>경기   

         통합 분류3 사건/사고 분류1 사건/사고 분류2  ...  \
0      경제>산업_기업       NaN       NaN  ...   
1           NaN       NaN       NaN  ...   
2        경제>자동차       NaN       NaN  ...   
3         지역>경남       NaN       NaN  ...   
4           NaN       NaN       NaN  ...   
...         ...       ...       ...  ...   
3646        NaN       NaN       NaN  ...   
3647        NaN       NaN       NaN  ...   
3648     경제>자동차       NaN       NaN  ...   
3649        NaN       NaN       NaN  ...   
3650      지역>강원       NaN       NaN  ...   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         키워드  \
0                                                                                     동원산업,환경,안전,최우선,실천,ESG,경영,한국,존경,기업,수산기업,최대,수산,기업,동원산업,경영,활동,확립,현장,안전,체계,ESG,경영,환경,사회,투명경영,박차,동원산업,글로벌,수산,기업,지속가능경영,논의,회의체,SeaBOS,Seafood,Business,Ocean,Stewardship,유일,한국,기업,해양,플라스틱,리더,기업,환경영향,저감,활동,안전,가치,안전,재해,통합,TF,설치,안전보건관리위원회,확대,개편,동원산업,노력,한국능률협회컨설팅,선정,한국,존경,기업,수산,1위,연속,동원산업,보전,해양,생태,환경,지역,사회,ESG,경영,일환,데이,국제,해안,클린업,International,Coastal,Clean-up,행사,진행,국제,해안,클린업,데이,행사,SeaBOS,회원사들,합의,감축,달성,해양,플라스틱,감축,달성,기획,국제,해안,클린업,데이,행사,서울,부산,해외,사업장,참여,진행,부산,임직원들,동원산업,부산지사,임직원,감천항,송도해수

In [82]:
# Loop through URLs, scrap information, identify the main body
# URL이 주어졌을 경우 해당 매체 웹사이트로부터 뉴스기사전문 크롤링

#최종결과물에 대한 텍스트 전처리-불용어 제거
#반복적인 불용어에 대한 메뉴얼 수정 내용 추가 - 미디어 매채별 예외처리 등록
def clean_html(raw_html):
    cleanr = re.compile('<.*?>|\s{2}|\n')
#    cleanr = re.compile('[^-가-힣a-zA-Z0-9/ ]')
    clean_text = re.sub(cleanr, '', raw_html)
    clean_text = clean_text.replace('window.jQuery || document.write("")', '')
    clean_text = clean_text.replace('Copyright ⓒ 동아일보 &amp; donga.com', '') #동아일보
    clean_text = clean_text.replace('좋아요 이미지좋아요슬퍼요 이미지슬퍼요화나요 이미지화나요후속기사 원해요 이미지후속기사 원해요기사추천 이미지기사추천공유 이미지공유공유하기닫기', '')
    clean_text = clean_text.replace('ⓒ 매일경제 &amp; mk.co.kr', '').replace('googletag.display("google_dfp_MC_250x250")', '').replace('googletag.display("google_dfp_MC_2x1,fluid")', '')
    clean_text = clean_text.replace('[', '').replace(']', '').replace('&amp', '').replace(', ■', '').replace('■ &lt', '').replace(';', '').replace('◆', '').replace('▲', '').replace('◇', '').replace('⊙', '')
    return clean_text


def crawling_main_text(url):
        
        if type(url)==float:
            content = 'n/a'
        
        
        #조선일보 - 미완성
        elif 'chosun' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})

            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            content_obj = soup.find_all("div", class_="article-body")
            
            
            content = clean_html(str(content_obj))
        
        
        #중앙일보
        elif 'joins' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})

            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')

            content_obj = soup.find_all('div', class_="article_body")
            content = clean_html(str(content_obj))
        
        
        #동아일보
        elif 'donga' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})

            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')

            content_obj = soup.find_all('div', class_="article_txt")
            content = clean_html(str(content_obj))
        
        
        #한겨례신문
        elif 'hani' in url:
            url = urllib.request.Request(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
            res = urllib.request.urlopen(url).read().decode("utf-8")
    
            soup = BeautifulSoup(res, "html.parser", from_encoding='utf-8')
            
            content_obj = soup.find_all('div', class_="text")
            content = clean_html(str(content_obj))
        

        #경향신문
        elif 'khan' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})

            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')

            content_obj = soup.find_all('p', class_="content_text")
            content = clean_html(str(content_obj))
        
        
        #한국경제
        elif 'hankyung' in url:
            try: 
                url = urllib.request.Request(url, headers=headers)
                res = urllib.request.urlopen(url).read().decode("utf-8")
    
                soup = BeautifulSoup(res, "html.parser")
    
                content_obj = soup.find_all('div', id="articletxt")
                content = clean_html(str(content_obj))
            except UnicodeDecodeError:
                content = 'NaN'
                pass
            except HTTPError:
                content = 'NaN'
                pass
        
        #매일경제
        elif 'mk' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})

            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            soup_alt = bs4.BeautifulSoup(url.content.decode('euc-kr', 'replace'), "html.parser")

            content_obj = soup_alt.find_all('div', class_="art_txt")

            content = clean_html(str(content_obj))
        
        #KBS
        elif 'kbs' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
            
            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            
            content_obj = soup.find_all('div', id="cont_newstext")
            content = clean_html(str(content_obj))
        
        #MBC
        elif 'imbc' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
            
            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            
            content_obj = soup.find('div', {'itemprop' : 'articleBody'})
            content = clean_html(str(content_obj))
        
        #OBS
        elif 'obsnews' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
            
            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            
            content_obj = soup.find_all('article', id="article-view-content-div")
            content = clean_html(str(content_obj))
        
        #SBS
        elif 'sbs' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
            
            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            
            content_obj = soup.find('div', {'itemprop' : 'articleBody'})
            content = clean_html(str(content_obj))
        
        #YTN
        elif 'ytn' or 'yonhap' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
            
            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            
            main_article = soup.find('div', {'itemprop' : 'articleBody'})
            if main_article == None:
                main_article = soup.find('div', {'class' : 'article=txt'})
                
            content = clean_html(str(main_article))
        
    
        return content
                                     

In [83]:
#For Loop을 통한 본문 크롤링
#데이터 프레임에 추가

df_news['main_content']='n/a'

for i, url in enumerate(df_news['URL']):
    print(url)
    print(type(url))
    try:
        main_body = crawling_main_text(url)
        print(main_body)
        df_news['main_content'].iloc[i] = main_body
    except ConnectionError:
        continue
    

http://news.mk.co.kr/newsRead.php?no=193115&year=2022
<class 'str'>


C:\Users\ohike\anaconda3\lib\site-packages\bs4\__init__.py:226: UserWarning: You provided Unicode markup but also provided a value for from_encoding. Your from_encoding will be ignored.
  warnings.warn("You provided Unicode markup but also provided a value for from_encoding. Your from_encoding will be ignored.")
C:\Users\ohike\AppData\Local\Temp\ipykernel_5032\2318398793.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_news['main_content'].iloc[i] = main_body


동원산업은 지난해 7월 안전재해통합TF 발대식을 진행하고 '자율 안전경영'을 선포하였다. 안전재해통합TF는 지난해 12월 안전보건관리위원회로 확대 개편되어 전사 사업장의 통합 안전 관리와 재해사고 예방을 위한 활동을 담당하고 있다. 중대재해처벌법, 산업안전보건법 등 관련 법규 준수와 보건정책의 선도적 시행, 중대재해 예방을 위한 안전보건 책임경영 환경 조성, 산업재해 예방을 위한 협력구조 개선, 안전 기본원칙과 지침 준수, 현장 중심의 안전보건활동 강화 등의 활동을 시행하고 있다. 최근에는 안전보건 업무만을 전담하는 안전보건관리팀을 설치하여 전사 안전보건 관리체계를 한층 강화하였으며, 위원회와 연계하여 전사 사업장 안전 확보와 건강한 일터를 만드는 데 최선의 노력을 다하고 있다., 무단전재 및 재배포 금지	의 바이오 집어장치로 변경하고, 수산물 보랭재인 아이스팩도 100% 물과 생분해성 소재를 사용한 친환경 아이스팩으로 전량 교체해 사용하고 있다. 최근에는 선단의 폐어망에서 발생하는 플라스틱 폐기물을 활용해 자동차 부품으로 만드는 등 플라스틱 감축은 물론 다양한 플라스틱 재활용 방안도 추진하고 있다.
https://www.hankyung.com/society/article/2020083170991
<class 'str'>
 강원도가 동원산업과 2000억원을 투입해 ‘스마트 연어 양식 클러스터’ 조성에 나선다.강원도는 2023년까지 양양군 현북면 중광정리 11만6824㎡에 친환경 스마트 육상 연어 양식 클러스터를 조성한다고 31일 발표했다. 클러스터는 두 단계로 나눠 조성된다. 1단계는 양식수조, 종묘·친어(치어보다 큰 어린 물고기) 연구개발센터 등이 들어선다. 2단계는 동원산업 프리미엄 제품 생산시설과 가공공장 등을 신설한다.동원산업은 신설되는 공장에 사물인터넷(IoT), 정보통신기술(ICT), 빅데이터 등 4차 산업혁명 기술을 접목해 육상 기반의 순환 유수식 양식 시설을 설치할 예정이다.연어 양식은 미래 먹거리 신성장동력 사업으로 꼽힌다. 그중에서도 세계 연

이상현 매경닷컴 기자, 무단전재 및 재배포 금지	 플라스틱을 사용하고 있다고 밝혔는데 제품 생산 과정에서 과대포장을 지양하고, 친환경 자재를 사용해달라는 등 기업의 노력을 요구하는 의견(45.3%)이 높은 것으로 조사됐다.각하다"고 생각하는 것으로 나타났다.다.골자다.
https://www.donga.com/news/article/all/20210827/108786233/1
<class 'str'>
롯데제과가 한솔제지와 지속 가능한 친환경 패키지 개발을 위한 업무협약(MOU)을 맺었다고 27일 밝혔다.롯데제과는 26일 오후 3시 서울 양평동 롯데제과 사옥에서 협약식을 갖고 향후 2년간 한솔제지의 친환경 포장재를 다방면으로 활용하고 양사간의 브랜드를 적극 홍보하며 관련 정보를 공유하기로 했다. 또 양사는 지난 2월 ‘카카오 판지’에 이어 새로운 친환경 소재를 개발하는 데 적극 협력하기로 했다. 앞서 양사는 카카오 부산물을 활용한 친환경 종이 포장재 ‘카카오 판지’를 공동 개발해 초콜릿 제품 패키지에 적용한 바 있다. 카카오 원두를 그대로 들여와 가공하는 업체는 롯데제과가 업계에서 유일하다. 이외에도 롯데제과는 한솔제지가 최근 개발한 기능성 용지 ‘프로테고(Protego)’와 PE-Free 컵 등 다양한 친환경 소재를 활용한 제품을 선보일 계획이다.민명기 롯데제과 대표는 “50여 년간 업계 1등 기업으로서 실력과 인지도를 쌓은 두 회사가 친환경이라는 화두를 가지고 하나의 팀이 되기 위해 만났다. 공통점이 많은 두 회사가 앞으로 100년 기업으로 가는 길에 서로 든든한 동반자가 될 수 있기를 바란다”며 말했다.윤우열 동아닷컴 기자 cloudancer@donga.com 구독윤우열 기자동아닷컴 디지털경제팀cloudancer@donga.com$(document).ready(function(){ scrap('select', 'reporter', 'cloudancer@donga.com', '윤우열')})$(document).on('click', '#btn_cloudancer

매일유업(대표 김선희)의 유기농·친환경 식품 브랜드 상하목장은 지난 4월 유기농 우유를 2배 농축한 유기농 아이스크림을 출시했다. 밀크·딸기 2종으로 출시된 상하목장 유기농 아이스크림은 상하목장 유기농 우유를 2배 농축해 진하면서도 깔끔한 맛을 느낄 수 있다. 가족·친구들과 함께 즐길 수 있는 대용량 파인트컵 474㎖, 부담 없는 미니컵 100㎖ 두 가지 용량이다., 상하목장은 전 제품에 좋은 원재료만 엄선해 사용하는 것을 원칙으로 한다. 상하목장 유기농 아이스크림도 유기농 원재료 함량이 99.7%에 달할 정도로 유기농 원료를 고집했다. 유기농 우유·유기농 크림·유기농 설탕 등이다. 진한 우유맛을 내기 위해 상하목장 유기농 우유를 2배 농축해 담았는데 474㎖ 파인트컵에는 상하목장 유기농 우유 200㎖ 2팩이 담겨 있는 셈이다. 딸기 아이스크림은 꿀벌이 자연수분한 국산 유기농 설향딸기를 사용해 더욱 산뜻한 맛을 느낄 수 있다., 실제로 제품을 이용한 소비자들도 진한 우유맛과 깔끔한 뒷맛에 긍정적인 반응을 보이고 있다. “인공적이지 않은 진한 우유맛” “시중 아이스크림과 달리 과하게 달지 않고 깔끔한 뒷맛” “밀도가 높아 쫀쫀하면서도 부드러운 느낌” 등의 평이다., 상하목장 유기농 아이스크림은 매일유업 네이버 브랜드스토어를 비롯한 주요 온라인 쇼핑몰 또는 대형마트, 창고형 매장, 전국 편의점에서 만나볼 수 있다.
https://www.joongang.co.kr/article/25081639
<class 'str'>
매일유업매일유업 상하목장이 유기농 우유를 2배 농축해 진하면서도 깔끔한 맛을 전하는 유기농 아이스크림 2종(밀크·딸기)을 출시했다. 사진 매일유업매일유업의 유기농·친환경 식품 브랜드 상하목장이 유기농 우유를 2배 농축해 진하면서도 깔끔한 맛을 전하는 유기농 아이스크림 2종(밀크·딸기)을 출시했다. 용량은 가족·친구와 함께 즐길 수 있는 대용량 파인트컵(474mL)과 부담 없는 미니 컵(100mL)의 두 가지다.건강하고 좋은 원재료만 엄선 상하목장은 전

...

디지털뉴스국 고득관 기자, 무단전재 및 재배포 금지	반기 가동을 목표로 연간 생산량 2만톤 규모의 폴리실리콘 설비를 건설하겠다고 밝혔다. GCL은 2019년에도 2만톤의 신규 설비를 가동할 예정이다.이충재 KTB투자증권 연구원은 "15달러/kg 수준인 우리나라 폴리실리콘 수출 가격 역시 17~18달러/kg 이상으로 상승할 가능성 높지 않다"라며 "우리 업체들은 15달러/kg 수준에서 큰 수익을 내기 힘들기 때문에 OCI의 실적 개선 가능성 역시 높지 않다"고 말했다.
nan
<class 'float'>
n/a
http://news.mk.co.kr/newsRead.php?year=2017&no=641781
<class 'str'>
디지털뉴스국 이가희 기자, 무단전재 및 재배포 금지	트럼프 대통령의 행보를 봤을때 태양광 전지에 대한 세이프가드는 발동될 가능성이 높다"며 "세이프가드 발동시 2018년 미국 태양광 모듈 수요는 큰 폭으로 감소할 수 있다"라고 분석했다.
nan
<class 'float'>
n/a
http://news.mk.co.kr/newsRead.php?year=2017&no=600473
<class 'str'>
최주욱 한국기업평가 전문위원은 ＂폴리실리콘 시장은 정책과 수급 등에 따른 가격변동성이 높아 업황에 대한 불확실성이 존재하지만 OCI는 원재료 조달처 다변화, 공정 개선을 통합 원부자재 투입량 절감, 에너지 효율화 등 다각적인 원가절감 노력으로 충분한 대응능력을 갖췄다＂라고 설명했다.박윤구 기자, 무단전재 및 재배포 금지	 공급과잉 이슈 등으로 실적이 크게 떨어지기도 했다. 하지만 지난해 폴리실리콘 부문의 생산효율성 개선, 판가 안정화 등으로 수익성이 회복됨에 따라 4년만에 흑자전환에 성공했다. 지난 2분기 OCI의 연결기준 매출액은 전년 동기 대비 5.4% 증가한 6994억원, 영업이익은 33.4% 줄어든 314억원 기록했다.
http://news.mk.co.kr/newsRead.php?year=2017&no=599395
<class 'st

 ‘수소 관련주’로 재조명받기 시작한롯데정밀화학롯데정밀화학61,300+3.03%자세히 보기이 사상 최고가를 경신했다. 롯데정밀화학이 생산하는 암모니아가 수소 운반 수단으로 부각되면서 주가를 밀어올렸다는 분석이 나온다.8일 롯데정밀화학은 8.19%(6000원) 오른 7만9300원에 거래를 마쳤다. 지난 7월 중순부터 한 달여간 숨고르기를 거친 롯데정밀화학은 지난달 23일부터 13거래일 동안 단 하루도 상승세가 꺾이지 않고 있다. 이 기간 주가는 23.71% 뛰었다.그간 탄탄한 실적이 주가를 이끌었다면 최근 들어 주가에 탄력을 붙인 것은 수소 테마다. 롯데정밀화학이 생산하는 암모니아는 분자 구조상 질소만 떼어내면 수소를 추출할 수 있어 수소 운반체로 주목받고 있다. 롯데정밀화학은 연 90만t의 암모니아를 유통하는 국내 시장 점유율 1위 기업이다. 이날 신동빈 롯데그룹 회장은 “롯데는 부생수소 생산능력 및 암모니아 인프라 확대 등 수소 밸류체인 전반에 걸쳐 역량을 강화하고 있다”고 밝혔다.3분기 실적 전망도 밝다. 매출의 3분의 1을 차지하는 염소 계열 제품의 가격이 상승하면서 수익성이 좋아지고 있다는 분석이다. 주요 상품인 에폭시수지 원료(ECH) 가격은 이달 들어 t당 1776달러까지 올랐다. 지난해 하반기 저점 대비 두 배 이상 높은 수준이다. 증권사들은 롯데정밀화학의 3분기 매출이 전년 동기 대비 38.8% 증가한 4395억원에 달할 것으로 예상하고 있다. 영업이익도 129.9% 급증한 595억원 수준이 될 것으로 전망했다.전문가들은 최근 가파르게 오른 롯데정밀화학 주가가 여전히 저평가돼 있다고 보고 있다. 롯데정밀화학의 12개월 선행 주가수익비율(PER)은 7.1배다. 수소 관련주 평균이 50배인 것을 고려하면 현저히 낮은 수준이라는 평가다. 한상원 대신증권 연구원은 “그린 암모니아를 통해 친환경 성장을 도모하고 실적도 개선되고 있는 반면 주가는 절대적으로 저평가됐다”며 “목표주가 12만원도 보수적인 수준”이라고 했다. 에프앤가이드에 따르면 롯데정밀화학의 

이영욱 기자, 무단전재 및 재배포 금지	름알데히드는 80%, 암모니아는 99.8%의 냄새를 제거해주는 것이 실험으로 확인됐다. 화장실, 식당, 주방 등 냄새가 많이 나는 곳에 사용 가능하며 노래방, 숙박업소 등 여러 사람들이 이용하는 밀폐된 공간에서 효과가 크다. 푸른솔 크린에어는 3월 말부터 전국 제비스코 대리점을 통해 만날 수 잇다.
http://news.mk.co.kr/newsRead.php?year=2017&no=820613
<class 'str'>
푸른솔에는 발암물질로 알려진 강한 독성의 유해중금속 포름알데히드(HCHO)가 전혀 함유되지 않았다.강남제비스코는 푸른솔에 대해 환경부로부터 환경표지 인증을 받았다. 한국공기청정협회의 친환경 건축자재 인증도 획득했다. 특히 내부 광택 도료 중에서 국내 최초로 친환경 건축자재 인증의 최고등급인 클로버 5개를 받았다.친환경 건축자재 인증은 실내공기 오염물질 방출량이 적은 제품에 부여된다. 면역력이 약한 환자나 어린 아이들이 머무는 병원, 유치원 등을 지을 때 사용하면 좋은 제품이라고 회사 측은 자평했다. 사용자의 작업 편의성을 높인 점도 눈에 띈다. 우선 점도 조절 기능이 강화됐다. 때문에 푸른솔은 도장 작업 중 흐름성 눈물자국이 발생할 가능성이 적다. 안료 침강 가능성도 최소화했다. 오랜 기간 보관한 뒤 다시 사용하려 할 때도 도막을 쉽게 형성시킬 수 있다. 또 우수한 표면 질감을 구현해 도장 마무리를 깔끔하게 할 수 있고, 색 분리 현상을 개선해 사용자의 작업 편의성을 높인 것도 푸른솔의 장점이다.강남제비스코는 이 같은 품질을 바탕으로 건축 전문가와 일반 소비자들로부터 푸른솔이 좋은 평가를 받고 있다고 전했다. 회사는 앞으로도 꾸준한 연구개발(RD)을 통해 다양한 친환경 제품을 선보일 계획이다. 또 건축문화 발전과 건축 환경 개선에도 앞장서겠다고 강조했다.한경우 디지털뉴스국 기자, 무단전재 및 재배포 금지	
http://news.mk.co.kr/newsRead.php?year=2017&no=753894
<cl

 GS건설이 국내에서 처음으로 수소 플랜트를 모듈로 제작해 미국에 수출한다. GS건설은 미국 캘리포니아에 건설될 예정인 신재생 그린수소 플랜트의 모듈 설계 및 제작에 참여하기 위해 현지 에너지기업인 SG H2랭커스터와 양해각서(MOU)를 체결했다고 24일 밝혔다.이번 사업은 SG H2에너지가 특수목적법인 SG H2랭커스터를 통해 캘리포니아 랭커스터에 신재생 그린수소 설비를 건설하는 프로젝트다. 연간 4만t의 폐기물 종이를 원료로 사용해 하루 11t의 그린수소 생산을 목표로 하고 있다. 이는 중형 수소차 약 1700대를 충전할 수 있는 용량이다.GS건설은 이번 사업에서 EPC(설계·시공·조달) 단계의 핵심인 수소 플랜트 모듈을 제작한다. 회사 관계자는 “국내에서 제작한 모듈을 운송해 설치하는 것으로 수소 플랜트 표준화에 성공했다는 데 의미가 있다”고 말했다. 투자비를 줄이고 공사 기간을 단축할 수 있다.이유정 기자 yjlee@hankyung.com 
https://www.donga.com/news/article/all/20220124/111412793/2
<class 'str'>
미국 ‘SG H2 에너지’ 주도 수소 플랜트 구축 사업랭케스터시에 하루 11톤 수소 생산 설비 구축GS건설 사업 핵심 ‘수소 플랜트 모듈’ 공급향후 SG H2 에너지 사업 참여 확대수소 플랜트 모듈 관련 설계·시공 표준화GS건설이 미국 캘리포니아에 신재생 그린수소 플랜트 모듈을 수출한다. 수소 플랜트를 ‘모듈’로 만들어 수출하는 것은 국내 건설사 최초다. 이번 사업 참여를 계기로 친환경 신사업 확대와 ESG(환경·사회·지배구조) 경영 강화를 가속화한다는 방침이다.GS건설은 미국 캘리포니아에 건설 예정인 신재생 그린수소 플랜트에 핵심인 모듈 설계 및 제작 참여를 위한 양해각서(MOU)를 ‘SG H2 랭케스터 LLC’와 체결했다고 24일 밝혔다. 해당 사업은 미국 소재 에너지업체 SG H2 에너지가 미국 캘리포니아 랭케스터(Lancaster)시에 신재생 그린수소 설비를 건설하는 프로젝트다.

NameError: name 'HTTPError' is not defined

In [85]:
#Export dataframe if necessary

df_news.to_excel("df_news_updated.xlsx")

In [ ]:
#Adjustment
df_news['main_content'] = df_news['main_content'].str.replace(r'[^A-Za-z0-9가-힣 ]', '')

  
  
  
  
  
## Reference Code for Individual Media Source  (Legacy; No Longer Updated)

### 한겨례

In [ ]:
import urllib.request
from bs4 import BeautifulSoup

def contents_hankyoreh():
    
    #샘플 기사 URL
    list_url = "https://www.hani.co.kr/arti/politics/politics_general/1038853.html"
    
    url = urllib.request.Request(list_url)
    res = urllib.request.urlopen(url).read().decode("utf-8")
    #print(res)
    
    soup = BeautifulSoup(res, "html.parser")
    params1 = []
    params2 = []
    
    for link1, link2 in zip(soup.find_all('p', class_="date-time"), soup.find_all('div', class_="text")):
        params1.append(link1.get_text())
        params2.append(link2.get_text())
        
    for i1, i2 in zip(params1, params2):
        #print(i1.strip(), end=' ')
        print(i2.strip())
        
contents_hankyoreh()
    

### 한국경제

In [ ]:
#한국경제와 같은 경우 

import re
import urllib.request
from bs4 import BeautifulSoup

def cleanhtml(raw_html):
    cleanr = re.compile('<.*?>|\s{2}|\n')
    cleantext = re.sub(cleanr, '', raw_html)
    return cleantext

def contents_hankyung():
    
    #샘플 기사 URL
    list_url = "https://www.hankyung.com/finance/article/2021122646691"
    
    url = urllib.request.Request(list_url, headers={'User-Agent': 'Custom'}) #
    res = urllib.request.urlopen(url).read().decode("utf-8")
    
    soup = BeautifulSoup(res, "html.parser")
    
    content_obj = soup.find_all('div', id="articletxt")
    content = cleanhtml(str(content_obj))
    return content
        

contents_hankyung()
    

In [ ]:
        #한국경제
        elif 'hankyung' in url:
            headers = {'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'}
            url = requests.get(url, headers=headers)

            soup = BeautifulSoup(url.content.decode('euc-kr', 'replace'), "html.parser", from_encoding='utf-8')
    
            content_obj = soup.find_all('div', id="articletxt")
            content = clean_html(str(content_obj))

### 경향신문

In [ ]:
#샘플 기사 URL
list_url = 'https://www.khan.co.kr/national/national-general/article/202204142115005'

def contents_kyunghyang(list_url):
    
    url = requests.get(list_url, headers={'User-Agent': 'Custom'})

    soup = BeautifulSoup(url.text, "html.parser")

    content_obj = soup.find_all('p', class_="content_text")

    content = cleanhtml(str(content_obj))
    return content

contents_kyunghyang(list_url)

### 동아일보

In [ ]:
list_url = 'https://www.donga.com/news/article/all/20220404/112693737/1'

def contents_donga(list_url):
    
    url = requests.get(list_url, headers={'User-Agent': 'Custom'})

    soup = BeautifulSoup(url.text, "html.parser")

    content_obj = soup.find_all('div', class_="article_txt")

    content = cleanhtml(str(content_obj))
    return content

contents_donga(list_url)

### 중앙일보

In [ ]:
list_url = 'https://news.joins.com/article/2137057'

def contents_joongang(list_url):
    
    url = requests.get(list_url, headers={'User-Agent': 'Custom'})

    soup = BeautifulSoup(url.text, "html.parser")

    content_obj = soup.find_all('div', class_="article_body")

    content = cleanhtml(str(content_obj))
    return content

contents_joongang(list_url)

### 매일경제

In [ ]:
import bs4
list_url = 'https://www.mk.co.kr/news/stock/view/2022/04/339384/'

def contents_maeil(list_url):
    
    url = requests.get(list_url, headers={'User-Agent': 'Custom'})

    soup = BeautifulSoup(url.text, "html.parser", from_encoding='')
    soup_alt = bs4.BeautifulSoup(url.content.decode('euc-kr', 'replace'), "html.parser")

    content_obj = soup_alt.find_all('div', class_="art_txt")

    content = clean_html(str(content_obj))
    return content

contents_maeil(list_url)

### 조선일보

In [ ]:
!pip install selenium

In [ ]:
#조선일보 같은 경우 셀레니움 패키지를 사용

import re
import requests
from bs4 import BeautifulSoup
import urllib.request
import selenium
from selenium import webdriver

options = webdriver.ChromeOptions()
options.add_argument('--headless')
options.add_argument('--no-sandbox')
options.add_argument('--disable-dev-shm-usage')

#driver = webdriver.Chrome(ChromeDriverManager().install())

list_url = 'https://www.chosun.com/economy/stock-finance/2021/12/10/OYYDOUAR35HZHBIOO5YAL4XTD4/?utm_source=bigkinds&utm_medium=original&utm_campaign=news'

content_obj = []

#Legacy Component
def contents_chosun(list_url):
    
    url = requests.get(list_url, headers={'User-Agent': 'Custom'})

    soup = BeautifulSoup(url.text, "html.parser")
    print(soup)
    content_obj = soup.find_all('p')
    print(content_obj)
    
    content = clean_html(str(content_obj))
    
    if soup.select_one('#text'):
        soup.dl.extract()
        news_article = soup.select_one('#article').text
        print(news_article)
    
#    for tag in soup.select('#text'):
#        print(tag.text)
#        write_ws.append([tag.text])
    
#    content = clean_html(str(content_obj))
    return content

contents_chosun(list_url)

In [ ]:
#셀레니윰을 통한 조선일보 크롤링 접근

from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
import time

import pandas as pd
from selenium.common.exceptions import NoSuchElementException

list_url = 'https://www.chosun.com/economy/stock-finance/2021/12/10/OYYDOUAR35HZHBIOO5YAL4XTD4/?utm_source=bigkinds&utm_medium=original&utm_campaign=news'

content = []


#Selenium Component
driver = webdriver.Chrome(executable_path='/Users/ohikendoit/chromedriver', options=options)
driver.get(list_url)

driver.implicitly_wait(time_to_wait=5)
print(driver)

#more = driver.find_element_by_id('load-more-stories')

#for _ in range(120):
#    more.click()
#    time.sleep(1)
    
#selector = '#artwrapper > div > figure > div > div > div'
#a = driver.find_element(selector)

try:
    content_section = driver.find_element('//*[@id="fusion-app"]/div[1]/div[2]/div/section/article/section')
    p = content_section.find_elements('p')
    temp = []
    for item in p:
        temp.append(item.text)
    content.append('\n'.join(temp))
except:
    content.append(pd.NA)

driver.close()

## 셀레니움을 통한 조선일보 크롤링 구현

In [ ]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
import time
import pandas as pd
from selenium.common.exceptions import NoSuchElementException

In [ ]:
driver = webdriver.Chrome(executable_path='/Users/ohikendoit/chromedriver', options=options)
try:
    driver.get("https://www.google.com/")
except Exception as e:
    print(e.message)

In [ ]:
driver.get("https://www.google.com/")

In [ ]:
start_date = '20200501'
end_date = '20200502'
paper = 1023

num = 1
while True:
    driver.get(f'https://search.naver.com/search.naver?where=news&query=%EC%A7%80%EC%97%AD%ED%99%94%ED%8F%90&sm=tab_opt&sort=0&photo=0&field=0&pd=3&ds={start_date[0:4]}.{start_date[4:6]}.{start_date[6:]}&de={end_date[0:4]}.{end_date[4:6]}.{end_date[6:]}&docid=&related=0&mynews=1&office_type=1&office_section_code=1&news_office_checked={paper}&nso=so%3Ar%2Cp%3Afrom{start_date}to{end_date},a:all&start={num}')
    time.sleep(3)
    
    try:
        ul = driver.find_element(By.CSS_SELECTOR, '#main_pack > section > div > div.group_news > ul')
    except NoSuchElementException:
        print("Not exist paper")
        break
    lis = ul.find_elements(By.CLASS_NAME, 'li') #The previous approach has been depreciated.
    
    check = False
    
    for li in lis:
        tmp = li.get_attribute('id')
        tmp_url = driver.find_element(By.CSS_SELECTOR, f'#{tmp} > div > div > a').get_attribute("href")
        if tmp_url in url_list:
            check = True
            break
        url_list.append(tmp_url)
        
    if check:
        break
        
    num += 10

In [ ]:
url_list = ['https://biz.chosun.com/site/data/html_dir/2020/04/23/2020042302274.html?utm_source=bigkinds&utm_medium=original&utm_campaign=biz']

In [ ]:
for url in url_list:
    driver.get(url)
    time.sleep(1)
    content = driver.find_element_by_xpath('//*[@id="fusion-app"]/div[1]/div[2]/div/section/article/section').text
    print(content)
    
    print('='*30)
    print('='*30)